Test and Train archives webpage - https://learntoautofocus-google.github.io/

Path to your downloaded files. Store the files in a folder say 'Autofocus'. Then create a dirctory 'Train' as Autofocus/Train and store inside them downloaded folders which have name as 'train< number >' as Autofocus/Train/train< number >. Then create a ditrectory called 'Test' as Autofocus/Test and store the downloaded folder 'test' in it as Autofocus/Test/test

The code is made such that the user running the model needs to download the test archive and atleast 1 train dataset. Theres no need to download all train datasets all the increasing the number of train folders will increase accuracy. Copying a train folder and using that as a seperate folder (for example copying train1 and naming it train2 and using it) will not make any difference. Its the same as using only train1 but will of course consume more time to run.

In [1]:
autofocus_path='/mnt/Velocity Vault/Autofocus/'

autofocus_test_path=autofocus_path+"Test/"
autofocus_cache_path=autofocus_test_path+"Cache/"

In [2]:
import os
import pprint
import numpy as np
import random
import cv2
import OpenEXR
import Imath
from tqdm import tqdm
import copy
import time

In [3]:

def build_depth_map(super_path):
    depth_map_path = {}

    # Walk through the directory tree
    for root, _, files in os.walk(super_path):
        for filename in files:
            if filename.endswith('.png'):
                full_path = os.path.join(root, filename)
                # Remove super_path from the full path to get the relative path
                relative_path = os.path.relpath(full_path, super_path)
                # Split the relative path into parts (folders)
                parts = relative_path.split(os.sep)
                parts[-1]=parts[-1][len('result_merged_depth_'):-len('.png')]
                
                # Initialize nested dictionaries as needed
                current_dict = depth_map_path
                for part in parts[:-1]:  # Iterate over all parts except the last one (filename)
                    current_dict = current_dict.setdefault(part, {})
                
                # Assign the full path to the deepest nested dictionary
                current_dict[parts[-1]] = full_path

    return depth_map_path

def build_depth_map_confidence(super_path):
    depth_map_path = {}

    # Walk through the directory tree
    for root, _, files in os.walk(super_path):
        for filename in files:
            if filename.endswith('.exr'):
                full_path = os.path.join(root, filename)
                # Remove super_path from the full path to get the relative path
                relative_path = os.path.relpath(full_path, super_path)
                # Split the relative path into parts (folders)
                parts = relative_path.split(os.sep)
                parts[-1]=parts[-1][len('result_merged_conf_'):-len('.exr')]
                
                # Initialize nested dictionaries as needed
                current_dict = depth_map_path
                for part in parts[:-1]:  # Iterate over all parts except the last one (filename)
                    current_dict = current_dict.setdefault(part, {})
                
                # Assign the full path to the deepest nested dictionary
                current_dict[parts[-1]] = full_path

    return depth_map_path



In [4]:

train_path=[autofocus_test_path[:-1]]

print(len(train_path))
depth_map_path={}
depth_map_path_temp={}

for path in train_path:
    depth_map_path_temp=build_depth_map(path+"/merged_depth")
    depth_map_path.update(depth_map_path_temp)

depth_map_confidence_path={}
depth_map_confidence_path_temp={}

for path in train_path:
    depth_map_confidence_path_temp=build_depth_map_confidence(path+"/merged_conf")
    depth_map_confidence_path.update(depth_map_confidence_path_temp)

pprint.pprint(depth_map_path)
pprint.pprint(depth_map_confidence_path)

print(len(depth_map_path))


1
{'home1_0': {'bottom': '/mnt/Velocity '
                       'Vault/Autofocus/Test/merged_depth/home1_0/result_merged_depth_bottom.png',
             'center': '/mnt/Velocity '
                       'Vault/Autofocus/Test/merged_depth/home1_0/result_merged_depth_center.png',
             'left': '/mnt/Velocity '
                     'Vault/Autofocus/Test/merged_depth/home1_0/result_merged_depth_left.png',
             'right': '/mnt/Velocity '
                      'Vault/Autofocus/Test/merged_depth/home1_0/result_merged_depth_right.png',
             'top': '/mnt/Velocity '
                    'Vault/Autofocus/Test/merged_depth/home1_0/result_merged_depth_top.png'},
 'home1_1': {'bottom': '/mnt/Velocity '
                       'Vault/Autofocus/Test/merged_depth/home1_1/result_merged_depth_bottom.png',
             'center': '/mnt/Velocity '
                       'Vault/Autofocus/Test/merged_depth/home1_1/result_merged_depth_center.png',
             'left': '/mnt/Velocity '
    

In [5]:

def generate_random_patches(size=(504,378)):
    image=np.zeros(size)
    patches=[]
    for _ in (range(100)):
        x=random.randint(16, 487)
        y=random.randint(16, 361)

        #print(x,y)
        
        breaker=False

        for i in range(x-26,x+26):
            for j in range(y-26,y+26):
                if i<0 or i>503 or j<0 or j>377 :
                    continue
                if image[i][j]==1:
                    breaker=True
                    break
            if breaker:
                break

        if breaker:
            continue
        
        x=x-16
        y=y-16

        for i in range(x,x+33):
            for j in range(y,y+33):
                image[i][j]=1

        patches.append((x,y))


    return patches

In [6]:


def load_exr(file_path):
    exr_file = OpenEXR.InputFile(file_path)
    header = exr_file.header()
    dw = header['dataWindow']
    width = dw.max.x - dw.min.x + 1
    height = dw.max.y - dw.min.y + 1
    pt = Imath.PixelType(Imath.PixelType.FLOAT)
    r = np.frombuffer(exr_file.channel('R', pt), dtype=np.float32)
    r.shape = (height, width)
    return r

def predict_patches(depth_confidence_path):

    patch_threshold = 6

    depth_map_confidence = load_exr(depth_confidence_path)

    all_patches=generate_random_patches()

    confidence_patch_blocks=[depth_map_confidence[x:x+32,y:y+32] for (x,y) in all_patches]
    median_confidence_patch_block=[np.median(patch.flatten()) for patch in confidence_patch_blocks]

    patch_indices=[i for i, value in enumerate(median_confidence_patch_block) if value >= 0.98]

    if len(patch_indices)>4:
        patch_indices = sorted(range(len(median_confidence_patch_block)), key=lambda i: median_confidence_patch_block[i], reverse=True)[:patch_threshold]

    patches=[all_patches[patch_index] for patch_index in patch_indices]

    return patches

def predict_focal_length(depth_map_path,patch):
    depth_map = cv2.imread(depth_map_path, cv2.IMREAD_GRAYSCALE).astype(np.float32)

    depth_values=depth_map[patch[0]:patch[0]+32,patch[1]:patch[1]+32]
    depth_values=depth_values.flatten()

    # Define max and min values
    max_depth = 100.0
    min_depth = 0.2

    depth_map_in_meters = (max_depth * min_depth) / (max_depth - (max_depth - min_depth) * (depth_values / 255.0))

    # Compute the median value in the entire depth map
    median_depth = np.median(depth_map_in_meters)

    final_focus=median_depth*1000

    return final_focus

slice_focal_length=[3910.92,2289.27,1508.71,1185.83,935.91,801.09,700.37,605.39,546.23,486.87,447.99,407.40,379.91,350.41,329.95,307.54,291.72,274.13,261.53,247.35,237.08,225.41,216.88,207.10,198.18,191.60,183.96,178.29,171.69,165.57,160.99,155.61,150.59,146.81,142.35,138.98,134.99,131.23,127.69,124.99,121.77,118.73,116.40,113.63,110.99,108.47,106.54,104.23,102.01]

def find_closest(value, num_list):
    closest_value = min(num_list, key=lambda x: abs(x - value))
    return closest_value

def predict_slice(depth_map_path,depth_confidence_path):
    truth=[]

    patches=predict_patches(depth_confidence_path)
    
    for patch in patches:
        predicted_focus=predict_focal_length(depth_map_path,patch)
        closest_value = find_closest(predicted_focus, slice_focal_length)
        true_slice=slice_focal_length.index(closest_value)
        # manual annotation
        # true_slice=true_slice-1 if true_slice !=0 else true_slice
        truth.append((patch[0],patch[1],true_slice))

    return truth

In [7]:

ground_truth=copy.deepcopy(depth_map_path)

for image_type in tqdm(ground_truth):
    for pos in ground_truth[image_type]:
        ground_truth[image_type][pos]=predict_slice(depth_map_path[image_type][pos],depth_map_confidence_path[image_type][pos])

pprint.pprint(ground_truth)

100%|██████████| 47/47 [00:05<00:00,  8.09it/s]

{'home1_0': {'bottom': [(392, 243, 11), (428, 26, 5), (50, 245, 13)],
             'center': [(421, 280, 9),
                        (471, 76, 5),
                        (68, 238, 4),
                        (368, 90, 10),
                        (408, 13, 4),
                        (232, 215, 10)],
             'left': [(357, 28, 3),
                      (459, 38, 5),
                      (229, 299, 4),
                      (435, 211, 9),
                      (62, 273, 5),
                      (138, 285, 12)],
             'right': [(422, 149, 8),
                       (59, 213, 4),
                       (350, 8, 3),
                       (419, 80, 4),
                       (86, 259, 4),
                       (322, 127, 12)],
             'top': [(383, 188, 11),
                     (267, 276, 4),
                     (403, 28, 3),
                     (464, 72, 4),
                     (459, 15, 4),
                     (443, 172, 7)]},
 'home1_1': {'bottom': [(383, 133, 

In [8]:
patch_count=[]

for key1 in ground_truth:
    for key2 in ground_truth[key1]:
        patch_count.append(len(ground_truth[key1][key2]))

print(min(patch_count)," ",np.mean(patch_count)," ",max(patch_count))

0   5.323404255319149   6


In [9]:
def generate_image_paths(super_path):
    # Initialize the dictionary
    image_path = {}

    # Traverse the directory structure
    for root, dirs, files in os.walk(super_path):
        for file in files:
            if file.endswith('.png'):
                # Get the relative path from super_path
                relative_path = os.path.relpath(root, super_path)
                # Split the relative path to get <string> and <integer>
                string_part, integer_part = os.path.split(relative_path)
                integer_part = int(integer_part)
                
                # Extract the position from the filename
                file_name_parts = file.split('_')
                position = file_name_parts[-1].split('.')[0]  # Extract 'bottom', 'top', etc.
                
                # Construct the full file path
                full_file_path = os.path.join(root, file)
                
                # Populate the dictionary
                if string_part not in image_path:
                    image_path[string_part] = {}
                if integer_part not in image_path[string_part]:
                    image_path[string_part][integer_part] = {}
                
                image_path[string_part][integer_part][position] = full_file_path

    return image_path



In [10]:

left_image_path = {}
left_image_path_temp = {}
right_image_path = {}
right_image_path_temp = {}

train_path=[autofocus_test_path[:-1]]
print(len(train_path))


for path in train_path:
    left_image_path_temp = generate_image_paths(path+'/raw_up_left_pd')
    left_image_path.update(left_image_path_temp)
    right_image_path_temp = generate_image_paths(path+'/raw_up_right_pd')
    right_image_path.update(right_image_path_temp)


1


In [11]:
def reorder_image_path(image_path):
    ip = {}

    for key1, level2_dict in image_path.items():
        for key2, level3_dict in level2_dict.items():
            for key3, value in level3_dict.items():
                if key1 not in ip:
                    ip[key1] = {}
                if key3 not in ip[key1]:
                    ip[key1][key3] = []
                ip[key1][key3].append(value)

    return ip

left_image_path=reorder_image_path(left_image_path)
right_image_path=reorder_image_path(right_image_path)

pprint.pprint(left_image_path)
pprint.pprint(right_image_path)
print(len(left_image_path))
print(len(right_image_path))



{'home1_0': {'bottom': ['/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/29/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/0/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/1/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/10/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/11/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/12/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/13/result_up_pd_left_bottom.

In [12]:
def combine_path(left_path,right_path):
    path=[]
    for i in range(len(left_path)):
        path.append(left_path[i])
        path.append(right_path[i])
    
    return path

def combine_image_paths(left_image_path,right_image_path):
    image_paths=copy.deepcopy(left_image_path)
    for key1 in image_paths:
        for key2 in image_paths[key1]:
            image_paths[key1][key2]=combine_path(left_image_path[key1][key2],right_image_path[key1][key2])
    return image_paths

image_paths=combine_image_paths(left_image_path,right_image_path)

pprint.pprint(image_paths)
print(len(image_paths))
print(type(image_paths['home1_0']['center']))
print(len(image_paths['home1_0']['center']))

{'home1_0': {'bottom': ['/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/29/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_right_pd/home1_0/29/result_up_pd_right_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/0/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_right_pd/home1_0/0/result_up_pd_right_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/1/result_up_pd_left_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_right_pd/home1_0/1/result_up_pd_right_bottom.png',
                        '/mnt/Velocity '
                        'Vault/Autofocus/Test/raw_up_left_pd/home1_0/10/result_up_pd_left_bot

In [13]:
def check_dimension(arr):
    # Ensure the array has the correct shape
    s=len(arr.shape)
    if s!=2:
        print("Input array must have shape AxB")
    
    return arr

def combine_last_dimension(arrays):
    A = arrays[0].shape[0]  # Assuming all arrays have the same shape AxA
    s = len(arrays)
    
    # Initialize the resulting array with lists
    list_array = np.empty((A, A, s), dtype=object)
    
    # Fill the array with corresponding elements from each input array
    for k, array in enumerate(arrays):
        list_array[..., k] = array
    
    return list_array


In [14]:
def build_labels(ground_truth):
    labels=[]

    for image_type in tqdm(ground_truth):
        for pos in ground_truth[image_type]:
            temp=ground_truth[image_type][pos]
            truth=[z for (_,_,z) in temp]

            for i in range(len(truth)):
                labels.append(truth[i])

    return labels

labels_RAM=build_labels(ground_truth)

# pprint.pprint(labels)
print(len(labels_RAM))

100%|██████████| 47/47 [00:00<00:00, 194794.75it/s]

1251


In [15]:
def build_patch_count(ground_truth):
    patch_count=[]

    for image_type in tqdm(ground_truth):
        for pos in ground_truth[image_type]:
            count=len(ground_truth[image_type][pos])
            patch_count.append(count)

    return patch_count

patch_RAM=build_patch_count(ground_truth)

# pprint.pprint(labels)
print(len(patch_RAM))

100%|██████████| 47/47 [00:00<00:00, 517407.58it/s]

235


In [16]:
_dataset_len=len(labels_RAM)

filename=autofocus_cache_path+"labels.dat"
shape=(_dataset_len)
labels = np.memmap(filename, dtype='int8', mode='w+', shape=shape)

for index,label in enumerate(labels_RAM):
    labels[index]=label

labels.flush()

filename=autofocus_cache_path+"patch.dat"
shape=(len(patch_RAM))
patch_count = np.memmap(filename, dtype='int8', mode='w+', shape=shape)

for index,patch in enumerate(patch_RAM):
    patch_count[index]=patch

patch_count.flush()

In [17]:

def sleep_with_progress(seconds,index):
    print("Start Sleeping",seconds,"seconds -",index)
    time.sleep(seconds)
    print("End Sleeping -",index)

def wait_for_file(filepath, check_interval=1):
    while not os.path.isfile(filepath):
        time.sleep(check_interval)
    return 0

def build_dataset(filename,shape,image_paths,ground_truth):

    wait_for_file(filename)
    dataset=np.memmap(filename, dtype='int8', mode='r+', shape=shape)
    data_count=0
    count=0
    sleep_index=60
    for image_type in tqdm(ground_truth):
        if count%sleep_index==0 and count!=0:
            sleep_with_progress(60,count//sleep_index)
        count+=1
        for pos in ground_truth[image_type]:
            temp=ground_truth[image_type][pos]
            patches=[(x,y) for (x,y,_) in temp]

            try:
                all_images=[check_dimension(cv2.imread(path,0)) for path in image_paths[image_type][pos]]
            except Exception as e:
                print("Reconnect Drive")
                checker=[wait_for_file(path) for path in image_paths[image_type][pos]]
                all_images=[check_dimension(cv2.imread(path,0)) for path in image_paths[image_type][pos]]

            for i in range(len(patches)):
                x=patches[i][0]*4
                y=patches[i][1]*4

                images=[image[x:x+128,y:y+128]for image in all_images]

                image_set=combine_last_dimension(images)
                image_array=np.array(image_set,dtype='int8')

                wait_for_file(filename)
                dataset[data_count]=image_array            
                wait_for_file(filename)
                dataset.flush()
                data_count+=1


filename=autofocus_cache_path+"dataset.dat"
shape=(_dataset_len,128,128,98)
dataset=np.memmap(filename, dtype='int8', mode='w+', shape=shape)

build_dataset(filename,shape,image_paths,ground_truth)

# pprint.pprint(dataset)
print(len(dataset))


100%|██████████| 47/47 [11:42<00:00, 14.94s/it]

1251


In [18]:

def check_shapes(lst):
    target_shape = (128, 128, 98)
    for element in lst:
        if not isinstance(element, np.ndarray) or element.shape != target_shape:
            return False
    return True

print(dataset[0].shape)
print(check_shapes(dataset))

print(len(dataset))

(128, 128, 98)
True
1251


In [19]:
# dataset_len=22678

def save_variable_to_file(variable, filename):
    try:
        with open(filename, 'w') as file:
            file.write(str(variable))
        print(f"Variable saved successfully to {filename}")
    except Exception as e:
        print(f"Error occurred while saving variable to {filename}: {e}")

save_variable_to_file(_dataset_len,autofocus_cache_path+"length.dat")


Variable saved successfully to /mnt/Velocity Vault/Autofocus/Test/Cache/length.dat
